# Mega API 測試 Notebook

## 1. 限制

1. 期貨無預約單功能，請在各盤別交易時間下單
2. 期權市場不可於其他平台交互下單，如果當日在其他平台委託(如兆豐贏家、理財通等...) API下單則會鎖定，還是可以在其他平台處理委託單，下一個交易日API下單才會解鎖
3. 期權市場不支援複式單
4. 選擇權市場不支援個股選擇選商品交易
5. 期權市場只有自動倉
6. 僅固定式保證金支援市價單
7. 無保證金最佳化
8. 每秒委託限制20筆，超過的委託會被拒絕
9. API委託的錯誤單在其他平台查不到


## 2. 測試環境下單

1. 期權下單時間: 10:40-13:45、15:40-隔日05:00
2. 如近月商品無法下單或成交時請改下遠月
3. 開通期權的客戶需完成委託刪單、減量、改價、成交測試(可下市價單與市場的其他人成交或者自己下買單和賣單成交)


## 3. 範例需修改地方

第一個程式區塊，修改個人資料

## 4. 正式環境連線

當測試報告書完成後且收到公司通知已開通，如要下單到正式環境需修改以下兩個連線

1. speedyAPI_config.json裡的spapitest 改為 spapi
2. function ObjOrder.Connect 裡的 spapitest 改為 spapi

## 5. Notebook 說明
本 Notebook 將證券、期貨及選擇權的委託、刪單、改單（改價或減量）測試流程拆分為多個 Cell，
使用預先定義好的參數進行測試，並確認委託與成交回報。

**注意：**
1. 期貨下單時 TWSEOrdTyp 傳空字串。
2. 委託成功後，回報中的 `OrderID` 與 `SendNewOrderEx` 回傳的 `nid` 不同；取消及改單時需使用回報中的 `OrderID`。

## 6. 其他知識點(python)

- **Python 模組與 package：**
  本程式碼使用了 Mega API 的 Python package（例如 `megaSpeedy.spdOrderAPI`），
  並假設你已依照官方說明將相應 package 放置到 Python 的環境中（或虛擬環境內的 site-packages 目錄）。
- **logging 模組：**
  用於記錄訊息與除錯資訊，設定了輸出格式與等級，方便觀察程式執行狀態。
- **回傳結果處理：**
  API 回傳的結果通常為 JSON 格式，利用 `json.dumps` 可以格式化輸出，
  而使用 Pandas 將 list 轉 DataFrame 可方便檢視資料表格形式的內容。


In [6]:
import time
import os
import logging

# 設定 logging 格式與等級
logging.basicConfig(level=logging.INFO, format='%(asctime)s %(levelname)s: %(message)s')
logging.info('初始化環境完成')

# 請將以下變數值，改為自己的資料
UID='A123456789' #身分證字號字母大寫
LoginPW='1234' #登入密碼
FUBranchid='F030000' #期貨公司別(下單用) 不用修改
FUBranchid2='098' #期貨公司別(帳務用) 不用修改
FUAcc='1234567' #期貨帳號
CAPath='1234.pfx' #憑證路徑
CAPW='A123456789' #憑證密碼 ，測試環境預設同身分證字號
Symbol='TMFD5' #請修改成當年度當月份的商品代號，詳細商品代碼組成可參考下方期貨代碼命名規則

2025-04-14 15:53:27,621 INFO: 初始化環境完成


In [7]:
from megaSpeedy.spdOrderAPI import spdOrderAPI

class testPyOrderAPI(spdOrderAPI):
    """
    Speedy API 測試類別
    """
    def __init__(self):
        super().__init__()
        self.FIsLogon = False
        self.lastOrderID = None  # 用來儲存最新委託回報中的 OrderID

    def OnConnected(self):
        logging.info('-------------- OnConnected() --------------')
        # 使用憑證內的帳號 (此處範例使用 "A123456789")
        # self.LogonProxy('身分證字號(大寫字母)', '電子登入密碼', '證券帳號七位數如:[0023456]')
        # self.LogonProxy('身分證字號(大寫字母)', '電子登入密碼', '期貨帳號七位數如:[0023456]')
        # 登入證期市場逗號分隔
        # self.LogonProxy('身分證字號(大寫字母)', '電子登入密碼', '證券帳號七位數如:[0023456],期貨帳號七位數如:[0023456]')
        if not self.LogonProxy(UID, LoginPW, FUAcc):        
            logging.error(f'登入失敗! {self.GetLastErrorMsg()}')
            raise Exception("條件不符，中斷執行！")

    def OnDisconnected(self):
        logging.info('-------------- OnDisconnected() --------------')
        self.FIsLogon = False

    def OnLogonResponse(self, IsSucceed, ReplyString):
        logging.info('-------------- OnLogonResponse() --------------')
        logging.info(f'--- IsSucceed: {IsSucceed} ReplyString: {ReplyString}')
        if IsSucceed:
            self.FIsLogon = True
            # 期貨帳號設定
            # --------------交易所代碼不變、修改分公司代碼及證券帳號
            self.SetAccount('TAIFEX', FUBranchid, FUAcc)
            # 證券帳號設定
            self.SetAccount('TWSE', '7000', '0123456')
            # 複委託帳號設定
            self.SetAccount('US', '7000', '023456')
        else:
            logging.error(f"登入失敗. {ReplyString}")

    def OnReplyNewOrder(self, NID, UDD, Symbol, Price, Side, OrderQty, OrderType, TimeInForce, OrderID):
        logging.info('-------------- OnReplyNewOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} Symbol: {Symbol} Price: {Price} Side: {Side}')
        logging.info(f'--- OrderQty: {OrderQty} OrderType: {OrderType} TimeInForce: {TimeInForce} OrderID: {OrderID}')
        # 儲存回報中的 OrderID，供取消或改單使用
        self.lastOrderID = OrderID

    def OnReplyCancelOrder(self, NID, UDD, Symbol, Price, Side, OrderID):
        logging.info('-------------- OnReplyCancelOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} Symbol: {Symbol} Price: {Price} Side: {Side} OrderID: {OrderID}')

    def OnReplyReplaceOrder(self, NID, UDD, Symbol, Price, Side, OrderQty, OrderType, TimeInForce, OrderID):
        logging.info('-------------- OnReplyReplaceOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} Symbol: {Symbol} Price: {Price} Side: {Side}')
        logging.info(f'--- OrderQty: {OrderQty} OrderType: {OrderType} TimeInForce: {TimeInForce} OrderID: {OrderID}')

    def OnRejectOrder(self, NID, UDD, ActionFrom, ErrCode, ErrMsg):
        logging.info('-------------- OnRejectOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} ActionFrom: {ActionFrom} ErrCode: {ErrCode} ErrMsg: {ErrMsg}')

    def OnFill(self, NID, UDD, OrderID, ReportSequence, FillPrice, FillQty, FillTime):
        logging.info('-------------- OnFill() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} OrderID: {OrderID} ReportSequence: {ReportSequence}')
        logging.info(f'--- FillPrice: {FillPrice} FillQty: {FillQty} FillTime: {FillTime}')

In [8]:
# 實例化 API 物件，並設定憑證
ObjOrder = testPyOrderAPI()
# 請確保 A123456789.pfx 憑證檔案放置於工作目錄下
#ObjOrder.EnableMEGACA("憑證檔路徑","身分證字號(大寫字母)","憑證密碼")
result = ObjOrder.EnableMEGACA(CAPath, UID , CAPW )
if result:
    logging.info('已成功設定簽章憑證')
    logging.info('連線中...')
else:
    logging.error(f'簽章憑證設定失敗! {ObjOrder.GetLastErrorMsg()}')
    raise Exception("條件不符，中斷執行！")

ObjOrder.Connect('spapitest.emega.com.tw', 56789, 5)


#以下為自動重連範例，請先確認個人資料都正確才使用，不然帳號會因為錯誤次數太多而被鎖定
"""
Count = 0
while True:
    time.sleep(1)
    if Count % 10 == 0:
        if not ObjOrder.IsConnected():
            ObjOrder.Connect('spapitest.emega.com.tw', 56789, 5)
    Count += 1
    if ObjOrder.FIsLogon:
        logging.info('登入成功！')
        break
logging.info('連線及登入程序完成')
"""

2025-04-14 15:53:35,661 INFO: 已成功設定簽章憑證
2025-04-14 15:53:35,661 INFO: 連線中...


"\nCount = 0\nwhile True:\n    time.sleep(1)\n    if Count % 10 == 0:\n        if not ObjOrder.IsConnected():\n            ObjOrder.Connect('spapitest.emega.com.tw', 56789, 5)\n    Count += 1\n    if ObjOrder.FIsLogon:\n        logging.info('登入成功！')\n        break\nlogging.info('連線及登入程序完成')\n"

2025-04-14 15:53:47,142 INFO: -------------- OnConnected() --------------
2025-04-14 15:53:48,668 INFO: -------------- OnLogonResponse() --------------
2025-04-14 15:53:48,669 INFO: --- IsSucceed: True ReplyString: Login Mega DMA OK!( CID =19 )...logon ok


## 期貨代碼命名規則
- **大台**：`TXF`，**小台**：`MXF`
- **月份對應**：A=1月, B=2月, C=3月, D=4月, E=5月, F=6月, G=7月, H=8月, I=9月, J=10月, K=11月, L=12月
- **年份尾碼**：取西元年最後一碼。例如 2025 年尾碼為 `5`

因此，若要表示 2025 年 1 月份的大台指數期貨，則代碼為：
```
TXFA5
```
（`TXF` + `A` + `5`）

## 選擇權

- TXO
- 買權月份 : A=1月, B=2月, C=3月, D=4月, E=5月, F=6月, G=7月, H=8月, I=9月, J=10月, K=11月, L=12月
- 賣權月份 : M=1月, N=2月, O=3月, P=4月, Q=5月, R=6月, S=7月, T=8月, U=9月, V=10月, W=11月, X=12月

TXO+履約價+月份對應+年份尾碼
如: TXO23300B5

## 期貨測試流程 (請依序執行下面各個 Cell)

In [9]:
# 期貨新單委託測試
futures_order = {
    "Market": "fut",
    "Symbol": Symbol,  # 規則 (大台2025年1月) -> TXFA5
    "Price": 18000,
    "Qty": 3,
    "Side": "B",
    "OrderType": "L",
    "Tif": "R",
    "TS": "N",
    "PE": "A",
    "TO": ""  # 期貨下單 TWSEOrdTyp 請留空
}

futures_new_nid = ObjOrder.SendNewOrderEx(
    futures_order["Market"],
    "testUDD_New",
    futures_order["Symbol"],
    futures_order["Price"],
    futures_order["Side"],
    futures_order["Qty"],
    futures_order["OrderType"],
    futures_order["Tif"],
    futures_order["TS"],
    futures_order["PE"],
    futures_order["TO"]
)

if futures_new_nid == 0:
    logging.error(f"期貨新單委託失敗: {ObjOrder.GetLastErrorMsg()}")
else:
    logging.info(f"期貨新單委託成功, nid={futures_new_nid}")
    logging.info(f"取得的 OrderID 為: {ObjOrder.lastOrderID}")

2025-04-14 15:53:59,460 INFO: 期貨新單委託成功, nid=153
2025-04-14 15:53:59,460 INFO: 取得的 OrderID 為: None
2025-04-14 15:53:59,825 INFO: -------------- OnReplyNewOrder() --------------
2025-04-14 15:53:59,826 INFO: --- NID: 153 UDD:  Symbol: TMFD5 Price: 18000.0 Side: B
2025-04-14 15:53:59,827 INFO: --- OrderQty: 3 OrderType: L TimeInForce: R OrderID: d0003


In [10]:
# 期貨改單委託測試 - 改價測試
# 前提：已成功下單且回調中已存入 lastOrderID

if ObjOrder.lastOrderID is None:
    logging.error('未取得期貨新單回報的 OrderID，無法執行改價測試')
else:
    replace_order_price = {
        "Market": futures_order["Market"],
        "Symbol": futures_order["Symbol"],
        "Price": futures_order["Price"] + 10,  # 改價：價格 + 10
        "Qty": 0,           
        "Side": futures_order["Side"],
        "OrderID": ObjOrder.lastOrderID,
        "OrderType": futures_order["OrderType"],
        "Tif": futures_order["Tif"],
        "TS": futures_order["TS"],
        "TO": futures_order["TO"]  # 期貨下單 TWSEOrdTyp 留空
    }
    
    futures_replace_price_nid = ObjOrder.SendReplaceOrderEx(
        replace_order_price["Market"],
        "testUDD_Replace_Price",
        replace_order_price["Symbol"],
        replace_order_price["OrderID"],
        replace_order_price["Side"],
        replace_order_price["Price"],
        replace_order_price["Qty"],
        replace_order_price["OrderType"],
        replace_order_price["Tif"],
        replace_order_price["TS"],
        replace_order_price["TO"]
    )
    
    if futures_replace_price_nid == 0:
        logging.error(f"期貨改價委託失敗: {ObjOrder.GetLastErrorMsg()}")
    else:
        logging.info(f"期貨改價委託成功, nid={futures_replace_price_nid}")


2025-04-14 15:54:08,768 INFO: 期貨改價委託成功, nid=155
2025-04-14 15:54:09,158 INFO: -------------- OnReplyReplaceOrder() --------------
2025-04-14 15:54:09,160 INFO: --- NID: 155 UDD:  Symbol: TMFD5 Price: 18010.0 Side: B
2025-04-14 15:54:09,160 INFO: --- OrderQty: 0 OrderType: L TimeInForce: R OrderID: d0003


In [11]:
# 期貨改單委託測試 - 減量測試
# 前提：已成功下單且回調中已存入 lastOrderID
# 注意：若原始委託數量 futures_order["Qty"] 為 1，則減量後數量仍為 1（示範用）

if ObjOrder.lastOrderID is None:
    logging.error('未取得期貨新單回報的 OrderID，無法執行減量測試')
else:
    # 若原始數量大於 1，則減少 1；若只有 1，則保持不變
    new_qty = futures_order["Qty"] - 1 if futures_order["Qty"] > 1 else futures_order["Qty"]
    
    replace_order_qty = {
        "Market": futures_order["Market"],
        "Symbol": futures_order["Symbol"],
        "Price": futures_order["Price"],   # 價格保持不變
        "Qty": new_qty,                     # 新數量：減量後
        "Side": futures_order["Side"],
        "OrderID": ObjOrder.lastOrderID,
        "OrderType": futures_order["OrderType"],
        "Tif": futures_order["Tif"],
        "TS": futures_order["TS"],
        "TO": futures_order["TO"]           # 期貨下單 TWSEOrdTyp 留空
    }
    
    futures_replace_qty_nid = ObjOrder.SendReplaceOrderEx(
        replace_order_qty["Market"],
        "testUDD_Replace_Qty",
        replace_order_qty["Symbol"],
        replace_order_qty["OrderID"],
        replace_order_qty["Side"],
        replace_order_qty["Price"],
        replace_order_qty["Qty"],
        replace_order_qty["OrderType"],
        replace_order_qty["Tif"],
        replace_order_qty["TS"],
        replace_order_qty["TO"]
    )
    
    if futures_replace_qty_nid == 0:
        logging.error(f"期貨減量委託失敗: {ObjOrder.GetLastErrorMsg()}")
    else:
        logging.info(f"期貨減量委託成功, nid={futures_replace_qty_nid}")


2025-04-14 15:54:15,889 INFO: 期貨減量委託成功, nid=16539
2025-04-14 15:54:16,370 INFO: -------------- OnReplyReplaceOrder() --------------
2025-04-14 15:54:16,378 INFO: --- NID: 16539 UDD:  Symbol: TMFD5 Price: 0.0 Side: B
2025-04-14 15:54:16,379 INFO: --- OrderQty: 1 OrderType: L TimeInForce: R OrderID: d0003


In [12]:
# 期貨刪單委託測試
# 使用從新單回調中取得的 OrderID
if ObjOrder.lastOrderID is None:
    logging.error('未取得期貨新單回報的 OrderID，無法執行刪單測試')
else:
    cancel_order = {
        "Market": "fut",
        "Symbol": futures_order["Symbol"],
        "Price": futures_order["Price"],
        "Side": "B",
        "OrderID": ObjOrder.lastOrderID,
        "TS": "N",
        "TO": ""  
    }

    futures_cancel_nid = ObjOrder.SendCancelOrderEx(
        cancel_order["Market"],
        "testUDD_Cancel",
        cancel_order["Symbol"],
        cancel_order["Price"],
        cancel_order["Side"],
        cancel_order["OrderID"],
        cancel_order["TS"],
        cancel_order["TO"]
    )

    if futures_cancel_nid == 0:
        logging.error(f"期貨刪單委託失敗: {ObjOrder.GetLastErrorMsg()}")
    else:
        logging.info(f"期貨刪單委託成功, nid={futures_cancel_nid}")

2025-04-14 15:54:22,710 INFO: 期貨刪單委託成功, nid=154
2025-04-14 15:54:23,103 INFO: -------------- OnReplyCancelOrder() --------------
2025-04-14 15:54:23,107 INFO: --- NID: 154 UDD:  Symbol: TMFD5 Price: 18010.0 Side: B OrderID: d0003


## 選擇權測試流程 (請依序執行下面各個 Cell)

In [13]:
# 選擇權新單委託測試 (示範使用代碼 TXO06900B5)
# 其中 "Side": "S" 表示在 API 下單時為賣出，並非代表 put 權
options_order = {
    "Market": "opt",
    "Symbol": "TXO23300D5",  # 2025/2月買權，履約價23300
    "Price": 0.1,
    "Qty": 1,
    "Side": "B",             # 買進
    "OrderType": "L",        # 限價單
    "Tif": "R",              # ROD
    "TS": "N",               # Normal
    "PE": "A",               # PositionEffect
    "TO": ""                 # 期權下單 TWSEOrdTyp 留空
}

options_new_nid = ObjOrder.SendNewOrderEx(
    options_order["Market"],
    "testUDD_New",
    options_order["Symbol"],
    options_order["Price"],
    options_order["Side"],
    options_order["Qty"],
    options_order["OrderType"],
    options_order["Tif"],
    options_order["TS"],
    options_order["PE"],
    options_order["TO"]
)

if options_new_nid == 0:
    logging.error(f"選擇權新單委託失敗: {ObjOrder.GetLastErrorMsg()}")
else:
    logging.info(f"選擇權新單委託成功, nid={options_new_nid}")
    logging.info(f"取得的 OrderID 為: {ObjOrder.lastOrderID}")


2025-04-14 15:54:52,516 INFO: 選擇權新單委託成功, nid=16537
2025-04-14 15:54:52,518 INFO: 取得的 OrderID 為: d0003
2025-04-14 15:54:52,814 INFO: -------------- OnReplyNewOrder() --------------
2025-04-14 15:54:52,817 INFO: --- NID: 16537 UDD:  Symbol: TXO23300D5 Price: 0.1 Side: B
2025-04-14 15:54:52,817 INFO: --- OrderQty: 1 OrderType: L TimeInForce: R OrderID: d0004


In [14]:
# 選擇權刪單委託測試
if ObjOrder.lastOrderID is None:
    logging.error('未取得選擇權新單回報的 OrderID，無法執行刪單測試')
else:
    cancel_order_opt = {
        "Market": options_order["Market"],
        "Symbol": options_order["Symbol"],
        "Price": options_order["Price"],
        "Side": options_order["Side"],  # 與下單時相同
        "OrderID": ObjOrder.lastOrderID,  # 使用回調中取得的 OrderID
        "TS": options_order["TS"],
        "TO": options_order["TO"]
    }
    
    options_cancel_nid = ObjOrder.SendCancelOrderEx(
        cancel_order_opt["Market"],
        "testUDD_Cancel",
        cancel_order_opt["Symbol"],
        cancel_order_opt["Price"],
        cancel_order_opt["Side"],
        cancel_order_opt["OrderID"],
        cancel_order_opt["TS"],
        cancel_order_opt["TO"]
    )
    
    if options_cancel_nid == 0:
        logging.error(f"選擇權刪單委託失敗: {ObjOrder.GetLastErrorMsg()}")
    else:
        logging.info(f"選擇權刪單委託成功, nid={options_cancel_nid}")


2025-04-14 15:56:09,942 INFO: 選擇權刪單委託成功, nid=16538
2025-04-14 15:56:10,452 INFO: -------------- OnReplyCancelOrder() --------------
2025-04-14 15:56:10,454 INFO: --- NID: 16538 UDD:  Symbol: TXO23300D5 Price: 0.1 Side: B OrderID: d0004


In [15]:
# 選擇權新單委託測試 (示範使用代碼 TXO06900B5)
# 其中 "Side": "S" 表示在 API 下單時為賣出，並非代表 put 權
options_order = {
    "Market": "opt",
    "Symbol": "TXO23300D5",  # 2025/2月買權，履約價23300
    "Price": 0.1,
    "Qty": 10,
    "Side": "B",             # 買進
    "OrderType": "L",        # 限價單
    "Tif": "R",              # ROD
    "TS": "N",               # Normal
    "PE": "A",               # PositionEffect
    "TO": ""                 # 期權下單 TWSEOrdTyp 留空
}

options_new_nid = ObjOrder.SendNewOrderEx(
    options_order["Market"],
    "testUDD_New",
    options_order["Symbol"],
    options_order["Price"],
    options_order["Side"],
    options_order["Qty"],
    options_order["OrderType"],
    options_order["Tif"],
    options_order["TS"],
    options_order["PE"],
    options_order["TO"]
)

if options_new_nid == 0:
    logging.error(f"選擇權新單委託失敗: {ObjOrder.GetLastErrorMsg()}")
else:
    logging.info(f"選擇權新單委託成功, nid={options_new_nid}")
    logging.info(f"取得的 OrderID 為: {ObjOrder.lastOrderID}")


2025-04-14 15:56:35,214 INFO: 選擇權新單委託成功, nid=32921
2025-04-14 15:56:35,215 INFO: 取得的 OrderID 為: d0004
2025-04-14 15:56:35,483 INFO: -------------- OnReplyNewOrder() --------------
2025-04-14 15:56:35,489 INFO: --- NID: 32921 UDD:  Symbol: TXO23300D5 Price: 0.1 Side: B
2025-04-14 15:56:35,489 INFO: --- OrderQty: 10 OrderType: L TimeInForce: R OrderID: d0005


In [16]:
# 選擇權改單委託測試 - 改價測試
if ObjOrder.lastOrderID is None:
    logging.error('未取得選擇權新單回報的 OrderID，無法執行改單測試')
else:
    # 改價：將價格增加 5（例如從 200.0 改為 205.0）
    replace_order_opt = {
        "Market": options_order["Market"],
        "Symbol": options_order["Symbol"],
        "Price": options_order["Price"] + 5,  # 改為價格 + 5
        "Qty": 0,          
        "Side": options_order["Side"],
        "OrderID": ObjOrder.lastOrderID,
        "OrderType": options_order["OrderType"],
        "Tif": options_order["Tif"],
        "TS": options_order["TS"],
        "TO": options_order["TO"]
    }
    
    options_replace_nid = ObjOrder.SendReplaceOrderEx(
        replace_order_opt["Market"],
        "testUDD_Replace",
        replace_order_opt["Symbol"],
        replace_order_opt["OrderID"],
        replace_order_opt["Side"],
        replace_order_opt["Price"],
        replace_order_opt["Qty"],
        replace_order_opt["OrderType"],
        replace_order_opt["Tif"],
        replace_order_opt["TS"],
        replace_order_opt["TO"]
    )
    
    if options_replace_nid == 0:
        logging.error(f"選擇權改單委託失敗: {ObjOrder.GetLastErrorMsg()}")
    else:
        logging.info(f"選擇權改單委託成功, nid={options_replace_nid}")


2025-04-14 15:56:43,311 INFO: 選擇權改單委託成功, nid=32923
2025-04-14 15:56:43,666 INFO: -------------- OnReplyReplaceOrder() --------------
2025-04-14 15:56:43,668 INFO: --- NID: 32923 UDD:  Symbol: TXO23300D5 Price: 5.1 Side: B
2025-04-14 15:56:43,668 INFO: --- OrderQty: 0 OrderType: L TimeInForce: R OrderID: d0005


In [17]:
# 選擇權減量委託測試
# 注意：若原始委託數量 (options_order["Qty"]) 為 1，則減量後仍為 1（示範用例），
# 你可以根據實際情況調整數量以進行有效的減量測試。

if ObjOrder.lastOrderID is None:
    logging.error('未取得選擇權新單回報的 OrderID，無法執行減量測試')
else:
    # 如果原始數量大於 1，則減少 1；否則保持不變
    new_qty = options_order["Qty"] - 1 if options_order["Qty"] > 1 else options_order["Qty"]
    
    replace_order_qty = {
        "Market": options_order["Market"],
        "Symbol": options_order["Symbol"],
        "Price": options_order["Price"],   # 價格保持不變
        "Qty": new_qty,                     # 新數量 (減量後)
        "Side": options_order["Side"],
        "OrderID": ObjOrder.lastOrderID,
        "OrderType": options_order["OrderType"],
        "Tif": options_order["Tif"],
        "TS": options_order["TS"],
        "TO": options_order["TO"]           # 期權下單 TWSEOrdTyp 留空
    }
    
    options_reduce_nid = ObjOrder.SendReplaceOrderEx(
        replace_order_qty["Market"],
        "testUDD_Replace_Qty",
        replace_order_qty["Symbol"],
        replace_order_qty["OrderID"],
        replace_order_qty["Side"],
        replace_order_qty["Price"],
        replace_order_qty["Qty"],
        replace_order_qty["OrderType"],
        replace_order_qty["Tif"],
        replace_order_qty["TS"],
        replace_order_qty["TO"]
    )
    
    if options_reduce_nid == 0:
        logging.error(f"選擇權減量委託失敗: {ObjOrder.GetLastErrorMsg()}")
    else:
        logging.info(f"選擇權減量委託成功, nid={options_reduce_nid}")


2025-04-14 15:56:57,984 INFO: 選擇權減量委託成功, nid=49307
2025-04-14 15:56:58,357 INFO: -------------- OnReplyReplaceOrder() --------------
2025-04-14 15:56:58,360 INFO: --- NID: 49307 UDD:  Symbol: TXO23300D5 Price: 0.0 Side: B
2025-04-14 15:56:58,360 INFO: --- OrderQty: 1 OrderType: L TimeInForce: R OrderID: d0005


In [18]:
import json
import pandas as pd
from IPython.display import display, JSON
# 期貨委託查詢測試範例

# 建立查詢參數，所有參數皆為字串型態
query_param = {
    "branch_id": FUBranchid2,    # 分公司代碼 (必填)；期貨市場查詢分公司代碼為 098
    "cust_id": FUAcc,    # 客戶帳號 (必填)
    "type": "0",           # 查詢類別 (必填)： '0' 表示全部委託
    "apcode": ""          # 盤別：空字串表示全部，'C' 表示一般盤，'P' 表示盤後
}

# 呼叫 queryFutOrder 進行查詢，回傳結果為 JSON 格式
api_result = ObjOrder.queryFutOrder(query_param)

api_result = json.loads(api_result)

# 輸出查詢結果
logging.info("期貨委託查詢結果:")
logging.info(api_result)

if "dataList" in api_result and api_result["dataList"]:
    df = pd.DataFrame(api_result["dataList"])
    display(df)
    display(JSON(api_result))
else:
    logging.info("查詢結果無資料")


2025-04-14 15:57:12,076 INFO: Note: NumExpr detected 20 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
2025-04-14 15:57:12,077 INFO: NumExpr defaulting to 8 threads.
2025-04-14 15:57:12,336 INFO: 期貨委託查詢結果:
2025-04-14 15:57:12,337 INFO: {'result': '0', 'dataList': [{'v6': '155657', 'v7': 'B', 'v8': 'TXO', 'v9': '202504', 'v10': '000233000000', 'v12': '0010', 'v11': 'C', 'v14': '0', 'v13': '000000051000', 'v16': 'M', 'v15': 'R', 'v18': '0001', 'v17': '0009', 'v19': '0010', 'v21': '0009', 'v20': '0000', 'v23': '', 'v22': '0', 'v25': '20250415', 'v24': '2', 'v27': 'P', 'v1': 'TIM', 'v26': 'O', 'v2': 'PI', 'v3': '', 'v4': 'd0005', 'v5': '20250414'}, {'v6': '155609', 'v7': 'B', 'v8': 'TXO', 'v9': '202504', 'v10': '000233000000', 'v12': '0001', 'v11': 'C', 'v14': '0', 'v13': '000000001000', 'v16': 'C', 'v15': 'R', 'v18': '0000', 'v17': '0001', 'v19': '0001', 'v21': '0001', 'v20': '0000', 'v23': '', 'v22': '0', 'v25': '20250415', 'v24': '2', 'v27': 'P', 'v1': 'TIM', 'v2

v6 v7     v8      v9           v10   v12 v11 v14           v13 v16  \
0   155657  B    TXO  202504  000233000000  0010   C   0  000000051000   M   
1   155609  B    TXO  202504  000233000000  0001   C   0  000000001000   C   
2   155422  B    TMF  202504  000000000000  0001   F   0  000180100000   C   
3   155150  B    TMF  202504  000000000000  0000   F   0  000180000000   O   
4   153208  B  FIMTX  202504  000000000000  0000   F   0  000000000000   O   
5   141853  B    TJF  202505  000000000000  0001   F   0  000023107500   C   
6   141542  B    TJF  202505  000000000000  0003   F   0  000023007500   M   
7   140658  S    TJF  202505  000000000000  0000   F   0  000023007500   O   
8   140636  B    TJF  202505  000000000000  0000   F   0  000023007500   O   
9   140559  B    TJF  202504  000000000000  0000   F   0  000000000000   O   
10  103211  B  FIMTX  202504  000000000000  0000   F   0  000000000000   O   

    ... v22       v25 v24 v27   v1 v26  v2 v3     v4        v5  
0   ...   0  20250415   2   P  TIM   O  PI     d0005  20250414  
1   ...   0  20250415   2   P  TIM   O  PI     d0004  20250414  
2   ...   0  20250415   2   P  TIM   O  PI     d0003  20250414  
3   ...   0  20250415   2   P  TIM   O  PI     d0002  20250414  
4   ...   0  20250415   2   P  TIM   O  PI     d0001  20250414  
5   ...   0  20250414   2   C  TIM   C  PI     D0007  20250414  
6   ...   0  20250414   2   C  TIM   C  PI     D0006  20250414  
7   ...   0  20250414   2   C  TIM   O  PI     D0005  20250414  
8   ...   0  20250414   2   C  TIM   O  PI     D0004  20250414  
9   ...   0  20250414   2   C  TIM   O  PI     D0003  20250414  
10  ...   0  20250414   2   C  TIM   O  PI     D0002  20250414  

[11 rows x 27 columns]

<IPython.core.display.JSON object>

In [19]:
import json
import pandas as pd
from IPython.display import display, JSON
# 期貨成交查詢測試範例

# 建立查詢參數，所有參數皆為字串型態
query_param = {
    "branch_id": FUBranchid2,    # 分公司代碼 (必填)；期貨市場查詢分公司代碼為 098
    "cust_id": FUAcc,    # 客戶帳號 (必填)
    "type": "0",           # 查詢類別 (必填)： '0' 表示全部委託
    "apcode": ""          # 盤別：空字串表示全部，'C' 表示一般盤，'P' 表示盤後
}

# 呼叫 queryFutOrder 進行查詢，回傳結果為 JSON 格式
api_result = ObjOrder.queryFutMatch(query_param)

api_result = json.loads(api_result)

# 輸出查詢結果
logging.info("期貨成交查詢結果:")
logging.info(api_result)

if "dataList" in api_result and api_result["dataList"]:
    df = pd.DataFrame(api_result["dataList"])
    display(df)
    display(JSON(api_result))
else:
    logging.info("查詢結果無資料")

2025-04-14 15:57:15,659 INFO: 期貨成交查詢結果:
2025-04-14 15:57:15,662 INFO: {'result': '0', 'dataList': [{'v6': 'S', 'v7': 'TJF', 'v8': '202505', 'v9': '000000000000', 'v10': 'F', 'v20': '000000000000', 'v12': '000025022500', 'v11': '0001', 'v14': 'O', 'v13': '0', 'v16': 'C', 'v1': 'TIM', 'v15': '00300004', 'v2': 'PI', 'v18': '', 'v3': 'D0005', 'v17': '20250414', 'v4': '20250414', 'v5': '140658', 'v19': ''}], 'message': '執行成功'}


v6   v7      v8            v9 v10           v20           v12   v11 v14 v13  \
0  S  TJF  202505  000000000000   F  000000000000  000025022500  0001   O   0   

  v16   v1       v15  v2 v18     v3       v17        v4      v5 v19  
0   C  TIM  00300004  PI      D0005  20250414  20250414  140658

<IPython.core.display.JSON object>

In [20]:
import json
import pandas as pd
from IPython.display import display, JSON
# 期貨未平倉查詢測試範例

# 建立查詢參數，所有參數皆為字串型態
query_param = {
    "branch_id": FUBranchid2,    # 分公司代碼 (必填)；期貨市場查詢分公司代碼為 098
    "cust_id": FUAcc,    # 客戶帳號 (必填)
    "type": "0",           # 查詢類別 (必填)： '0' 表示全部委託
    "apcode": ""          # 盤別：空字串表示全部，'C' 表示一般盤，'P' 表示盤後
}

# 呼叫 queryFutOrder 進行查詢，回傳結果為 JSON 格式
api_result = ObjOrder.queryFutUncoverRT(query_param)

api_result = json.loads(api_result)

# 輸出查詢結果
logging.info("期貨未平倉查詢結果:")
logging.info(api_result)

if "dataList" in api_result and api_result["dataList"]:
    df = pd.DataFrame(api_result["dataList"])
    display(df)
    display(JSON(api_result))
else:
    logging.info("查詢結果無資料")

2025-04-14 15:57:21,774 INFO: 期貨未平倉查詢結果:
2025-04-14 15:57:21,775 INFO: {'result': '0', 'dataList': [{'v6': 'TJF', 'v7': '202505', 'v8': '000000000000', 'v9': 'F', 'v10': '0001', 'v12': '000024315000', 'v11': '000141500000', 'v14': 'N', 'v13': '000000000000', 'v16': '000000200000', 'v15': 'NTT', 'v18': '000000200000', 'v17': '000000100000', 'v19': '000000100000', 'v21': 'C', 'v20': '000140900000', 'v23': '14065936', 'v22': '20250414', 'v25': '0000', 'v24': '+0000000000', 'v27': '0001', 'v1': 'TIM', 'v26': '', 'v2': 'D000500', 'v3': '20250414', 'v4': '000025022500', 'v5': 'S'}], 'message': '執行成功'}


v6      v7            v8 v9   v10           v12           v11 v14  \
0  TJF  202505  000000000000  F  0001  000024315000  000141500000   N   

            v13           v16  ...       v22   v25          v24   v27   v1  \
0  000000000000  000000200000  ...  20250414  0000  +0000000000  0001  TIM   

  v26       v2        v3            v4 v5  
0      D000500  20250414  000025022500  S  

[1 rows x 27 columns]

<IPython.core.display.JSON object>

In [21]:
import json
import pandas as pd
from IPython.display import display, JSON
# 期貨權益查詢測試範例

# 建立查詢參數，所有參數皆為字串型態
query_param = {
    "branch_id": FUBranchid2,    # 分公司代碼 (必填)；期貨市場查詢分公司代碼為 098
    "cust_id": FUAcc,    # 客戶帳號 (必填)
    "type": "0",           # 查詢類別 (必填)： '0' 表示全部委託
    "apcode": ""          # 盤別：空字串表示全部，'C' 表示一般盤，'P' 表示盤後
}

# 呼叫 queryFutOrder 進行查詢，回傳結果為 JSON 格式
api_result = ObjOrder.queryMargin(query_param)

api_result = json.loads(api_result)

# 輸出查詢結果
logging.info("期貨權益查詢結果:")
logging.info(api_result)

if "dataList" in api_result and api_result["dataList"]:
    df = pd.DataFrame(api_result["dataList"])
    display(df)
    display(JSON(api_result))
else:
    logging.info("查詢結果無資料")

2025-04-14 15:57:27,390 INFO: 期貨權益查詢結果:
2025-04-14 15:57:27,391 INFO: {'result': '0', 'dataList': [{'v6': '00000000000000', 'v7': '+0000120000000', 'v8': '+0000000099999', 'v9': '00000000000000', 'v10': '+0000120000000', 'v20': '00000000000000', 'v12': '+0000000000000', 'v11': '+0000000000000', 'v14': '+0000000000000', 'v13': '+00000000000', 'v16': '+0000000000000', 'v1': 'CNY', 'v15': '+0000000000000', 'v2': '+0000120000000', 'v18': '+0000000000000', 'v3': '00000000000000', 'v17': '+0000000000000', 'v4': '00000000000000', 'v5': '00000000000000', 'v19': '00000000000000'}, {'v6': '00000000000000', 'v7': '+0001040000000', 'v8': '+0000000099999', 'v9': '00000000000000', 'v10': '+0001040000000', 'v20': '00000000000000', 'v12': '+0000000000000', 'v11': '+0000000000000', 'v14': '+0000000000000', 'v13': '+00000000000', 'v16': '+0000000000000', 'v1': 'JPT', 'v15': '+0000000000000', 'v2': '+0001040000000', 'v18': '+0000000000000', 'v3': '00000000000000', 'v17': '+0000000000000', 'v4': '00000000

v6              v7              v8              v9  \
0  00000000000000  +0000120000000  +0000000099999  00000000000000   
1  00000000000000  +0001040000000  +0000000099999  00000000000000   
2  00000000000000  +0039972593800  +0000000099999  00000000000000   
3  00000000000000  +0000080000000  +0000000099999  00000000000000   
4  00000000000000  +0043362435300  +0000000099999  00000000000000   

              v10             v20             v12             v11  \
0  +0000120000000  00000000000000  +0000000000000  +0000000000000   
1  +0001040000000  00000000000000  +0000000000000  +0000000000000   
2  +0039972596800  00000000000000  +0000001415000  +0000000000000   
3  +0000080000000  00000000000000  +0000000000000  +0000000000000   
4  +0043362438300  00000000000000  +0000001415000  +0000000000000   

              v14           v13             v16   v1             v15  \
0  +0000000000000  +00000000000  +0000000000000  CNY  +0000000000000   
1  +0000000000000  +00000000000  +0000000000000  JPT  +0000000000000   
2  +0000000000000  +00000030000  +0000000000000  NTD  +0000000027500   
3  +0000000000000  +00000000000  +0000000000000  UST  +0000000000000   
4  +0000000000000  +00000030000  +0000000000000       +0000000027500   

               v2             v18              v3             v17  \
0  +0000120000000  +0000000000000  00000000000000  +0000000000000   
1  +0001040000000  +0000000000000  00000000000000  +0000000000000   
2  +0039957226300  +0000000000000  00000008770000  +0000000000000   
3  +0000080000000  +0000000000000  00000000000000  +0000000000000   
4  +0043347067800  +0000000000000  00000008770000  +0000000000000   

               v4              v5             v19  
0  00000000000000  00000000000000  00000000000000  
1  00000000000000  00000000000000  00000000000000  
2  00000006685000  00000000000000  00000000000000  
3  00000000000000  00000000000000  00000000000000  
4  00000006685000  00000000000000  00000000000000

<IPython.core.display.JSON object>

# 中斷連線

從jupyter釋放資源

In [13]:
# 測試完畢後斷線並結束程序
ObjOrder.Disconnect()
logging.info('~~~ Program terminate ~~~')

2025-02-13 13:09:05,654 INFO: ~~~ Program terminate ~~~


# 行情測試

`修改行情主機IP:QuoteIP`


In [24]:
from megaSpeedy.spdQuoteAPI import spdQuoteAPI
import time, os

QuoteIP='0.0.0.0'

#----------------------------------------------------------------------------
# spdQuoteAPI implementation
#----------------------------------------------------------------------------
class testPyQuoteAPI(spdQuoteAPI):
    def OnConnected(self):
        # implement OnConnected() ...
        print('-------------- OnConnected() --------------')
    def OnDisconnected(self):
        #implement OnDisconnected() ...
        print('-------------- OnDisConnected() --------------')
        pass
    def OnLogonResponse(self, IsSucceed, ReplyString):
        #implement OnLogonResponse() ...
        print('-------------- OnLogonResponse() --------------')
        print('--- IsSucceed:{0} ReplyString:{1}'.format(IsSucceed, ReplyString))                
        global logonOK
        logonOK = IsSucceed        
        pass
    def OnContractDownloadComplete(self):        
        print('-------------- OnContractDownloadComplete() --------------')        
        if Symbol in self.Futures:
            Contract = self.Futures[Symbol]
            self.Subscribe( Contract.Exchange , Contract.Symbol )
            Contract.Print()
        pass
    def OnOrderBook(self, Exchange, Symbol, MsgTime, Msg):
        #implement OnOrderBook() ...
        print('-------------- OnOrderBook() --------------')
        print('--- Exchange[{0}]  Symbol[{1}]  MsgTime[{2}]'.format(Exchange, Symbol, MsgTime))
        print('--- Bid1={0}({1})  Bid2={2}({3})  Bid3={4}({5})  Bid4={6}({7})  Bid5={8}({9})'.format(
            Msg.BidPrice1, Msg.BidQty1, Msg.BidPrice2, Msg.BidQty2, Msg.BidPrice3, Msg.BidQty3, Msg.BidPrice4, Msg.BidQty4, Msg.BidPrice5, Msg.BidQty5))
        print('--- Ask1={0}({1})  Ask2={2}({3})  Ask3={4}({5})  Ask4={6}({7})  Ask5={8}({9})'.format(
            Msg.AskPrice1, Msg.AskQty1, Msg.AskPrice2, Msg.AskQty2, Msg.AskPrice3, Msg.AskQty3, Msg.AskPrice4, Msg.AskQty4, Msg.AskPrice5, Msg.AskQty5))
        print('--- DerivedBid={0}({1})  DerivedAsk={2}({3})'.format(Msg.DerivedBidPrice, Msg.DerivedBidQty, Msg.DerivedAskPrice, Msg.DerivedAskQty))
        print(f'--- IsTestMatch={Msg.IsTestMatch}');
        pass
    def OnTrade(self, Exchange, Symbol, MatchTime, MatchPrice, MatchQty, IsTestMatch):
        #implement OnTrade() ...
        print('-------------- OnTrade() --------------')
        print('--- Exchange[{0}]  Symbol[{1}]'.format(Exchange, Symbol))
        print('--- MatchTime={0}  MatchPrice={1}  MatchQty={2}'.format(MatchTime, MatchPrice, MatchQty))
        print(f'--- IsTestMatch={IsTestMatch}');
        pass

In [25]:
logonOK = False
ObjQuote = testPyQuoteAPI()

print('IsConnected:', str(ObjQuote.IsConnected()))    
#testPyQuoteAPI.py說明:
#訂閱檔數上限20檔
#ObjQuote.Logon('IP', 34567, '身分證字號(大寫字母)', '電子登入密碼', True )
#取消訂閱商品:ObjQuote.UnsubscribeAll()

if not ObjQuote.Logon(QuoteIP, 34567, UID, LoginPW, True ):
    print(f'登入失敗! {ObjQuote.GetLastErrorMsg()}') 
print('IsConnected:', str(ObjQuote.IsConnected()))

IsConnected: False
-------------- OnConnected() --------------
IsConnected: True
-------------- OnLogonResponse() --------------
--- IsSucceed:True ReplyString:Logon OK!
Total Contract Count [77592] 
-------------- OnContractDownloadComplete() --------------
----- [TAIFEX][TMFD5] -----
Exchange[TAIFEX] 
Symbol[TMFD5] 
Market[fut] 
DisplayName[TMFD5] 
Category[TMF] 
BullPx[21446.0] 
BearPx[17548.0] 
RefPx[19497.0] 
ContractMultiplier[10.0] 
MaturityDate[202504] 
CallPut[None] 
StrikePx[0.0] 
----- TW Futures -----
-------------- OnOrderBook() --------------
--- Exchange[TAIFEX]  Symbol[TMFD5]  MsgTime[15:58:33.903]
--- Bid1=19539.0(2)  Bid2=19538.0(2)  Bid3=19537.0(7)  Bid4=19536.0(46)  Bid5=19535.0(12)
--- Ask1=19540.0(2)  Ask2=19541.0(4)  Ask3=19542.0(41)  Ask4=19543.0(6)  Ask5=19544.0(1)
--- DerivedBid=0.0(0)  DerivedAsk=19542.0(2)
--- IsTestMatch=False
-------------- OnOrderBook() --------------
--- Exchange[TAIFEX]  Symbol[TMFD5]  MsgTime[15:58:34.028]
--- Bid1=19539.0(2)  Bid2=195

In [26]:
# 退訂商品
ObjQuote.UnsubscribeAll()

-------------- OnOrderBook() --------------
--- Exchange[TAIFEX]  Symbol[TMFD5]  MsgTime[15:58:37.153]
--- Bid1=19539.0(5)  Bid2=19538.0(5)  Bid3=19537.0(7)  Bid4=19536.0(46)  Bid5=19535.0(15)
--- Ask1=19541.0(43)  Ask2=19542.0(2)  Ask3=19543.0(6)  Ask4=19544.0(1)  Ask5=19545.0(10)
--- DerivedBid=0.0(0)  DerivedAsk=19542.0(2)
--- IsTestMatch=False
